In [101]:
import sys, os, importlib, json
import folium, shapely

import pandas as pd
import geopandas as gpd

from shapely.geometry import Polygon, Point, mapping
from shapely.ops import unary_union
from urllib.request import urlopen

In [10]:
official_wb_bounds = "/home/public/Data/GLOBAL/ADMIN/Admin0_Polys.shp"
geobounds_url = 'https://www.geoboundaries.org/api/current/gbOpen/{iso3}/ADM{lvl}/'

In [36]:
# Need to wait on whitelisting for this to work
'''
response = urlopen(geobounds_url.format(iso3='UGA',lvl='1'))
data_json = json.loads(response.read())
data_json
'''
local_bounds = "/home/wb411133/projects/BOUNDARIES/geoBoundaries-UGA-ADM1.geojson"
inGeo = gpd.read_file(local_bounds)

In [12]:
inWB = gpd.read_file(official_wb_bounds)

# Select WB data and map

In [27]:
selWB = inWB.loc[inWB['ISO3'] == 'UGA']
selWB = selWB.to_crs(4326)

In [49]:
# Generate slivers, or holes in the geobounds that are in the WB bounds
wb_slivers = selWB.unary_union.difference(inGeo.unary_union)

In [69]:
cnt = 0
all_res = []
for sliver in list(wb_slivers):
    all_res.append([cnt, sliver, sliver.area])
    
wb_sliver_df = gpd.GeoDataFrame(pd.DataFrame(all_res, columns=['ID','geometry','area']), geometry='geometry', crs=4326)
wb_sliver_df = wb_sliver_df.to_crs(3857)
wb_sliver_df['area'] = wb_sliver_df['geometry'].apply(lambda x: x.area/1000000)
wb_sliver_df = wb_sliver_df.to_crs(4326)
big_slivers = wb_sliver_df.loc[wb_sliver_df['area'] > 100]
wb_sliver_df = wb_sliver_df.loc[wb_sliver_df['area'] < 100]



/tmp/ipykernel_22973/1830888155.py:3: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for sliver in list(wb_slivers):
/tmp/ipykernel_22973/1830888155.py:3: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for sliver in list(wb_slivers):


In [71]:
inGeo

shapeName shapeISO                  shapeID shapeGroup shapeType  \
0  Northern Region     UG-N  17295835B76470662483631        UGA      ADM1   
1   Eastern Region     UG-E  17295835B16269990444989        UGA      ADM1   
2   Central Region     UG-C     17295835B43600399901        UGA      ADM1   
3   Western Region     UG-W  17295835B38632472727119        UGA      ADM1   

                                            geometry  
0  POLYGON ((34.78710 1.36522, 34.79309 1.37101, ...  
1  MULTIPOLYGON (((33.66433 -0.13367, 33.66777 -0...  
2  MULTIPOLYGON (((33.39414 0.23746, 33.39586 0.2...  
3  POLYGON ((31.35819 2.24848, 31.35820 2.24520, ...

In [91]:
# For each sliver, determine the admin1 section to merge it into
inGeo_id = 'shapeISO'
wb_sliver_df['geoID'] = ''
for idx, row in wb_sliver_df.iterrows():
    sel_geo = inGeo.loc[inGeo.intersects(row['geometry'].buffer(0.01))]
    if sel_geo.shape[0] == 1:
        wb_sliver_df.loc[idx, 'geoID'] = sel_geo[inGeo_id].values[0]
    else:
        # If it intersects two admins, figure out which one if intersects more
        sel_geo['area'] = sel_geo['geometry'].apply(lambda x: x.intersection(row['geometry'].buffer(0.01)).area)
        wb_sliver_df.loc[idx, 'geoID'] = sel_geo.sort_values('area', ascending=False).iloc[0][inGeo_id]
        
    

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/geopandas/geodataframe.py:1351: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [93]:
wb_sliver_df['geoID'].value_counts()

UG-W    467
UG-N    111
UG-E     49
Name: geoID, dtype: int64

In [114]:
# Loop through the geo_bounds
edit_geo = inGeo.copy()
for idx, row in edit_geo.iterrows():
    # Clip shape to national boundary
    new_shape = row['geometry'].intersection(selWB.unary_union)    
    
    # Select all the slivers to merge into the current admin area
    sel_slivers = wb_sliver_df.loc[wb_sliver_df['geoID'] == row[inGeo_id]]
    new_shape = new_shape.union(unary_union(sel_slivers['geometry']))
    row['geometry'] = new_shape
    edit_geo.loc[idx] = row

# Map results

In [120]:
# Generate h3 grid around dedicated city
m = folium.Map(location=[selWB.centroid.y.values[0], selWB.centroid.x.values[0]], zoom_start=7, tiles="stamentoner")

wb_shp = folium.GeoJson(mapping(selWB.unary_union), style_function=lambda feature: {
    'color':'green',
    'weight':4
}) 
wb_shp.add_to(m)


for idx, row in edit_geo.iterrows():
    geo_bounds = folium.GeoJson(mapping(row['geometry']), style_function=lambda feature: {
        'color':'red',
        'weight':1
    })
    geo_bounds.add_to(m)

map_slivers = folium.GeoJson(mapping(inGeo), style_function=lambda feature: {
    'color':'blue',
    'weight':0.5
}) 
map_slivers.add_to(m)

m

/tmp/ipykernel_22973/3025676840.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m = folium.Map(location=[selWB.centroid.y.values[0], selWB.centroid.x.values[0]], zoom_start=7, tiles="stamentoner")
/tmp/ipykernel_22973/3025676840.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m = folium.Map(location=[selWB.centroid.y.values[0], selWB.centroid.x.values[0]], zoom_start=7, tiles="stamentoner")
